In [10]:
import pandas as pd
import numpy as np
from collections import defaultdict
import warnings
warnings.filterwarnings('ignore')

def create_new_visit_area_mapping(df_visit, custom_residence_keywords=None, enable_residence_grouping=True):
    """
    방문지 정보에서 장소명과 주소를 기반으로 새로운 ID 매핑을 생성
    거주지 관련 키워드(집, 아파트, 빌라)가 포함된 장소는 모두 하나로 통합
    
    Args:
        df_visit: 방문지 정보 DataFrame
        custom_residence_keywords: 사용자 정의 거주지 키워드 리스트
        enable_residence_grouping: 거주지 통합 기능 사용 여부
    
    Returns:
        dict: 원본 ID -> 새 ID 매핑 딕셔너리
    """
    print("=== NEW_VISIT_AREA_ID 매핑 생성 시작 ===")
    
    # 1. 데이터 복사 및 전처리
    df = df_visit.copy()
    
    # 거주지 관련 키워드 정의
    if custom_residence_keywords:
        residence_keywords = custom_residence_keywords
    else:
        residence_keywords = ['집', '아파트', '빌라', '주택', '댁', '홈']
    
    def is_residence(name):
        """장소명이 거주지인지 확인"""
        if not name or not enable_residence_grouping:
            return False
        return any(keyword in name for keyword in residence_keywords)
    
    if enable_residence_grouping:
        print(f"거주지 키워드: {residence_keywords}")
    else:
        print("거주지 통합 기능이 비활성화되었습니다.")
    
    # 2. 주소가 있는 장소들의 주소 정보 수집 (같은 이름에 대한 기본 주소)
    address_by_name = {}
    
    for _, row in df.iterrows():
        name = str(row['VISIT_AREA_NM']).strip() if pd.notna(row['VISIT_AREA_NM']) else ''
        road_addr = str(row['ROAD_NM_ADDR']).strip() if pd.notna(row['ROAD_NM_ADDR']) else ''
        lot_addr = str(row['LOTNO_ADDR']).strip() if pd.notna(row['LOTNO_ADDR']) else ''
        
        # 거주지가 아닌 경우에만 주소 매핑 생성
        if name and (road_addr or lot_addr) and not is_residence(name):
            address = road_addr if road_addr else lot_addr
            if name not in address_by_name:
                address_by_name[name] = address
                print(f"기본 주소 등록: {name} -> {address}")
    
    # 3. 고유 장소 식별 및 주소 보완
    location_map = {}
    id_to_location_key = {}
    residence_ids = []  # 거주지 관련 ID들을 따로 수집
    
    for _, row in df.iterrows():
        visit_area_id = row['VISIT_AREA_ID']
        name = str(row['VISIT_AREA_NM']).strip() if pd.notna(row['VISIT_AREA_NM']) else ''
        road_addr = str(row['ROAD_NM_ADDR']).strip() if pd.notna(row['ROAD_NM_ADDR']) else ''
        lot_addr = str(row['LOTNO_ADDR']).strip() if pd.notna(row['LOTNO_ADDR']) else ''
        
        # 거주지 관련 장소는 특별 처리
        if is_residence(name):
            residence_ids.append({
                'id': visit_area_id,
                'name': name,
                'x_coord': row.get('X_COORD'),
                'y_coord': row.get('Y_COORD')
            })
            print(f"거주지 발견: {name} (ID: {visit_area_id})")
            continue
        
        # 일반 장소 처리
        # 주소가 없으면 같은 이름의 기본 주소 사용
        if not road_addr and not lot_addr and name in address_by_name:
            address = address_by_name[name]
            print(f"주소 보완: {name} (ID: {visit_area_id}) -> {address}")
        else:
            address = road_addr if road_addr else lot_addr
        
        # 고유 키 생성 (장소명 + 주소)
        location_key = f"{name}|{address}"
        
        # 위치 정보 저장
        if location_key not in location_map:
            location_map[location_key] = {
                'name': name,
                'address': address,
                'original_ids': [],
                'x_coord': row.get('X_COORD'),
                'y_coord': row.get('Y_COORD')
            }
        
        location_map[location_key]['original_ids'].append(visit_area_id)
        id_to_location_key[visit_area_id] = location_key
    
    # 4. 거주지들을 하나의 통합 장소로 처리
    if residence_ids and enable_residence_grouping:
        residence_key = "거주지|통합"
        location_map[residence_key] = {
            'name': '거주지(통합)',
            'address': '통합',
            'original_ids': [r['id'] for r in residence_ids],
            'x_coord': None,  # 통합된 거주지는 좌표 없음
            'y_coord': None
        }
        
        for residence in residence_ids:
            id_to_location_key[residence['id']] = residence_key
        
        print(f"거주지 통합 완료: {len(residence_ids)}개 ID를 하나로 통합")
        print(f"통합된 거주지 목록: {[r['name'] for r in residence_ids]}")
    elif residence_ids and not enable_residence_grouping:
        # 거주지 통합이 비활성화된 경우 일반 장소로 처리
        print(f"거주지 통합 비활성화: {len(residence_ids)}개 거주지를 개별 장소로 처리")
        for residence in residence_ids:
            visit_area_id = residence['id']
            name = residence['name']
            location_key = f"{name}|개별거주지"
            
            location_map[location_key] = {
                'name': name,
                'address': '개별거주지',
                'original_ids': [visit_area_id],
                'x_coord': residence['x_coord'],
                'y_coord': residence['y_coord']
            }
            id_to_location_key[visit_area_id] = location_key
    
    # 5. NEW_VISIT_AREA_ID 할당 (1부터 시작)
    new_id = 1
    id_mapping = {}
    location_to_new_id = {}
    
    for location_key, info in location_map.items():
        current_new_id = new_id
        location_to_new_id[location_key] = current_new_id
        
        # 해당 위치의 모든 원본 ID를 새 ID로 매핑
        for original_id in info['original_ids']:
            id_mapping[original_id] = current_new_id
        
        new_id += 1
    
    print(f"총 {len(id_mapping)}개의 원본 ID를 {new_id-1}개의 새 ID로 매핑")
    
    # 6. 중복 통계 출력
    duplicate_locations = [(k, v) for k, v in location_map.items() if len(v['original_ids']) > 1]
    duplicate_locations.sort(key=lambda x: len(x[1]['original_ids']), reverse=True)
    
    print(f"\n중복이 있는 장소: {len(duplicate_locations)}개")
    print("중복이 많은 상위 5개 장소:")
    for location_key, info in duplicate_locations[:5]:
        print(f"- {info['name']} ({info['address']}): {len(info['original_ids'])}개 ID")
    
    # 거주지 통합 정보 출력
    residence_location = next((v for k, v in location_map.items() if k.startswith("거주지|통합")), None)
    if residence_location:
        print(f"\n거주지 통합 결과:")
        print(f"- 통합된 거주지 개수: {len(residence_location['original_ids'])}개")
        print(f"- NEW_VISIT_AREA_ID: {location_to_new_id['거주지|통합']}")
    
    return id_mapping, location_map

def apply_new_id_to_visit_data(df_visit, id_mapping):
    """
    방문지 데이터에 NEW_VISIT_AREA_ID 적용
    """
    print("\n=== 방문지 데이터에 NEW_VISIT_AREA_ID 적용 ===")
    
    df_result = df_visit.copy()
    df_result['NEW_VISIT_AREA_ID'] = df_result['VISIT_AREA_ID'].map(id_mapping)
    
    # 매핑되지 않은 ID 확인
    unmapped = df_result[df_result['NEW_VISIT_AREA_ID'].isna()]
    if len(unmapped) > 0:
        print(f"경고: {len(unmapped)}개 행이 매핑되지 않음")
        print("매핑되지 않은 VISIT_AREA_ID:", unmapped['VISIT_AREA_ID'].unique())
    
    print(f"매핑 완료: {len(df_result)}개 행")
    return df_result

def apply_new_id_to_move_data(df_move, id_mapping):
    """
    이동내역 데이터에 NEW_VISIT_AREA_ID 적용
    """
    print("\n=== 이동내역 데이터에 NEW_VISIT_AREA_ID 적용 ===")
    
    df_result = df_move.copy()
    
    # START_VISIT_AREA_ID 매핑
    df_result['NEW_START_VISIT_AREA_ID'] = df_result['START_VISIT_AREA_ID'].map(id_mapping)
    
    # END_VISIT_AREA_ID 매핑  
    df_result['NEW_END_VISIT_AREA_ID'] = df_result['END_VISIT_AREA_ID'].map(id_mapping)
    
    # 매핑 결과 확인
    start_unmapped = df_result[pd.notna(df_result['START_VISIT_AREA_ID']) & 
                              pd.isna(df_result['NEW_START_VISIT_AREA_ID'])]
    end_unmapped = df_result[pd.notna(df_result['END_VISIT_AREA_ID']) & 
                            pd.isna(df_result['NEW_END_VISIT_AREA_ID'])]
    
    if len(start_unmapped) > 0:
        print(f"경고: {len(start_unmapped)}개 START_VISIT_AREA_ID가 매핑되지 않음")
    
    if len(end_unmapped) > 0:
        print(f"경고: {len(end_unmapped)}개 END_VISIT_AREA_ID가 매핑되지 않음")
    
    print(f"매핑 완료: {len(df_result)}개 행")
    
    # 이동 패턴 통계
    print("\n=== 이동 패턴 분석 ===")
    start_only = df_result[pd.notna(df_result['NEW_START_VISIT_AREA_ID']) & 
                          pd.isna(df_result['NEW_END_VISIT_AREA_ID'])]
    end_only = df_result[pd.isna(df_result['NEW_START_VISIT_AREA_ID']) & 
                        pd.notna(df_result['NEW_END_VISIT_AREA_ID'])]
    both = df_result[pd.notna(df_result['NEW_START_VISIT_AREA_ID']) & 
                    pd.notna(df_result['NEW_END_VISIT_AREA_ID'])]
    
    print(f"- 출발지만 있는 경우 (여행 시작): {len(start_only)}개")
    print(f"- 도착지만 있는 경우 (경유지): {len(end_only)}개") 
    print(f"- 출발지+도착지 모두 있는 경우: {len(both)}개")
    
    return df_result

def analyze_travel_patterns(df_move_updated):
    """
    여행 패턴 분석
    """
    print("\n=== 여행 패턴 상세 분석 ===")
    
    # 여행별 분석
    travel_stats = []
    
    for travel_id in df_move_updated['TRAVEL_ID'].unique():
        travel_data = df_move_updated[df_move_updated['TRAVEL_ID'] == travel_id].sort_values('START_DT_MIN')
        
        start_points = travel_data[pd.notna(travel_data['NEW_START_VISIT_AREA_ID'])]
        end_points = travel_data[pd.notna(travel_data['NEW_END_VISIT_AREA_ID'])]
        
        travel_stats.append({
            'TRAVEL_ID': travel_id,
            'total_moves': len(travel_data),
            'start_points': len(start_points),
            'end_points': len(end_points),
            'unique_locations': len(set(
                list(travel_data['NEW_START_VISIT_AREA_ID'].dropna()) + 
                list(travel_data['NEW_END_VISIT_AREA_ID'].dropna())
            ))
        })
    
    df_travel_stats = pd.DataFrame(travel_stats)
    
    print("여행별 통계:")
    print(f"- 평균 이동 횟수: {df_travel_stats['total_moves'].mean():.1f}")
    print(f"- 평균 방문 장소 수: {df_travel_stats['unique_locations'].mean():.1f}")
    print(f"- 최대 이동 횟수: {df_travel_stats['total_moves'].max()}")
    print(f"- 최대 방문 장소 수: {df_travel_stats['unique_locations'].max()}")
    
    return df_travel_stats

def main(custom_residence_keywords=None, enable_residence_grouping=True):
    """
    메인 실행 함수
    
    Args:
        custom_residence_keywords: 사용자 정의 거주지 키워드 리스트
        enable_residence_grouping: 거주지 통합 기능 사용 여부
    """
    try:
        # 1. 데이터 로드
        print("=== 데이터 로드 시작 ===")
        
        # 파일 읽기
        df_visit = pd.read_csv('./merged_csv/방문지_total.csv')
        df_move = pd.read_csv('./merged_csv/fin/이동내역_fin.csv')
        
        print(f"방문지 정보: {len(df_visit)} 행, {len(df_visit.columns)} 열")
        print(f"이동내역: {len(df_move)} 행, {len(df_move.columns)} 열")
        
        # 2. 데이터 미리보기
        print("\n=== 방문지 정보 샘플 ===")
        print(df_visit[['VISIT_AREA_ID', 'VISIT_AREA_NM', 'ROAD_NM_ADDR', 'LOTNO_ADDR']].head())
        
        print("\n=== 이동내역 샘플 ===")
        print(df_move[['TRAVEL_ID', 'START_VISIT_AREA_ID', 'END_VISIT_AREA_ID']].head())
        
        # 거주지 키워드 확인
        if enable_residence_grouping:
            if custom_residence_keywords:
                print(f"\n사용자 정의 거주지 키워드: {custom_residence_keywords}")
            else:
                print(f"\n기본 거주지 키워드: ['집', '아파트', '빌라', '주택', '댁', '홈']")
        
        # 3. NEW_VISIT_AREA_ID 매핑 생성
        id_mapping, location_map = create_new_visit_area_mapping(df_visit, custom_residence_keywords, enable_residence_grouping)
        
        # 4. 각 데이터에 새 ID 적용
        df_visit_updated = apply_new_id_to_visit_data(df_visit, id_mapping)
        df_move_updated = apply_new_id_to_move_data(df_move, id_mapping)
        
        # 5. 여행 패턴 분석
        df_travel_stats = analyze_travel_patterns(df_move_updated)
        
        # 6. 결과 저장
        print("\n=== 결과 저장 ===")
        df_visit_updated.to_csv('./merged_csv/fin/방문지_fin.csv', index=False, encoding='utf-8-sig')
        df_move_updated.to_csv('./merged_csv/fin/이동내역_fin.csv', index=False, encoding='utf-8-sig')
        df_travel_stats.to_csv('./merged_csv/fin/방문지_meta.csv', index=False, encoding='utf-8-sig')
        
        print("저장 완료:")
        print("- updated_visit_area_info.csv (방문지 정보 + NEW_VISIT_AREA_ID)")
        print("- updated_move_history.csv (이동내역 + NEW_START/END_VISIT_AREA_ID)")
        print("- travel_statistics.csv (여행별 통계)")
        
        # 7. 최종 요약
        print("\n=== 최종 요약 ===")
        print(f"총 고유 장소 수: {len(location_map)}")
        print(f"NEW_VISIT_AREA_ID 범위: 1 ~ {max(id_mapping.values())}")
        print(f"중복 제거된 장소 수: {len(df_visit) - len(location_map)}")
        
        return {
            'visit_data': df_visit_updated,
            'move_data': df_move_updated,
            'travel_stats': df_travel_stats,
            'id_mapping': id_mapping,
            'location_map': location_map
        }
        
    except Exception as e:
        print(f"오류 발생: {str(e)}")
        import traceback
        traceback.print_exc()
        return None

# 사용 예시들
def run_with_default_settings():
    """기본 설정으로 실행 (거주지 통합 포함)"""
    return main()

def run_without_residence_grouping():
    """거주지 통합 없이 실행"""
    return main(enable_residence_grouping=False)

def run_with_custom_keywords():
    """사용자 정의 키워드로 실행"""
    custom_keywords = ['집', '아파트', '빌라', '주택', '댁', '홈', '숙소', '펜션', '민박']
    return main(custom_residence_keywords=custom_keywords)

def find_residence_locations(df_visit):
    """
    현재 데이터에서 거주지로 분류될 장소들을 미리 확인하는 함수
    """
    residence_keywords = ['집', '아파트', '빌라', '주택', '댁', '홈']
    
    residence_locations = []
    for _, row in df_visit.iterrows():
        name = str(row['VISIT_AREA_NM']).strip() if pd.notna(row['VISIT_AREA_NM']) else ''
        if any(keyword in name for keyword in residence_keywords):
            residence_locations.append({
                'VISIT_AREA_ID': row['VISIT_AREA_ID'],
                'VISIT_AREA_NM': name,
                'ROAD_NM_ADDR': row.get('ROAD_NM_ADDR', ''),
                'LOTNO_ADDR': row.get('LOTNO_ADDR', '')
            })
    
    df_residence = pd.DataFrame(residence_locations)
    print(f"거주지로 분류될 장소: {len(df_residence)}개")
    if len(df_residence) > 0:
        print("\n거주지 목록:")
        for _, row in df_residence.iterrows():
            print(f"- {row['VISIT_AREA_NM']} (ID: {row['VISIT_AREA_ID']})")
    
    return df_residence

In [11]:
# 기본 실행 (거주지 통합 포함)
print("=== 기본 설정으로 실행 ===")
result = run_with_default_settings()

# 1. 거주지 통합 없이 실행
# result = run_without_residence_grouping()

# 2. 사용자 정의 키워드로 실행  
# result = run_with_custom_keywords()

# 3. 거주지 미리 확인해보기
# df_visit = pd.read_csv('tn_visit_area_info_방문지정보_F.csv')
# find_residence_locations(df_visit)

=== 기본 설정으로 실행 ===
=== 데이터 로드 시작 ===
방문지 정보: 140555 행, 23 열
이동내역: 140555 행, 9 열

=== 방문지 정보 샘플 ===
   VISIT_AREA_ID            VISIT_AREA_NM               ROAD_NM_ADDR  \
0     2304290001                        집                 유등로655번길27   
1     2304290002  아주 매운 공주 칼국수 주꾸미구이 신탄진점         대전 대덕구 덕암로222번길 34   
2     2304290003             청주 휴게소 서울 방향  충북 청주시 흥덕구 옥산면 경부고속도로 318   
3     2304290004                    갤럭시호텔              인천 중구 월미문화로 9   
4     2304290005                      월미도                        NaN   

                 LOTNO_ADDR  
0                       NaN  
1          대전 대덕구 덕암동 49-15  
2  충북 청주시 흥덕구 옥산면 장남리 282-6  
3        인천 중구 북성동1가 98-578  
4           인천 중구 북성동1가 산 1  

=== 이동내역 샘플 ===
   TRAVEL_ID  START_VISIT_AREA_ID  END_VISIT_AREA_ID
0  e_e000005         2.304290e+09                NaN
1  e_e000005                  NaN       2.304290e+09
2  e_e000005                  NaN       2.304290e+09
3  e_e000005                  NaN       2.304290e+09
4  e_e